### Ноутбук с обучением модели

In [1]:
import pandas as pd
import numpy as np
from transformers import AutoTokenizer
from datasets import load_dataset
from transformers import DataCollatorWithPadding, Trainer, TrainingArguments, AutoModelForSequenceClassification

In [2]:
tokenizer = AutoTokenizer.from_pretrained('roberta-base')

In [3]:
data_hf = load_dataset('csv', data_files={'train': 'data_train.csv',
                                          'test': 'data_test.csv'})
data_hf_tokenized = data_hf.map(lambda x: tokenizer(x['full_info'], max_length=512, truncation=True))
data_hf_tokenized = data_hf_tokenized.rename_column('tags', 'label')
data_hf_tokenized = data_hf_tokenized.remove_columns(['full_info'])

Using custom data configuration default-bd943fc5bb724360


Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

0 tables [00:00, ? tables/s]

0 tables [00:00, ? tables/s]

Dataset csv downloaded and prepared to /Users/seal/.cache/huggingface/datasets/csv/default-bd943fc5bb724360/0.0.0/51cce309a08df9c4d82ffd9363bbe090bf173197fc01a71b034e8594995a1a58. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

Parameter 'function'=<function <lambda> at 0x1641221f0> of the transform datasets.arrow_dataset.Dataset._map_single couldn't be hashed properly, a random hash was used instead. Make sure your transforms and parameters are serializable with pickle or dill for the dataset fingerprinting and caching to work. If you reuse this transform, the caching mechanism will consider it to be different from the previous calls and recompute everything. This warning is only showed once. Subsequent hashing failures won't be showed.


  0%|          | 0/11883 [00:00<?, ?ex/s]

  0%|          | 0/2097 [00:00<?, ?ex/s]

In [4]:
args_dict = {'output_dir': 'logs', 'per_device_train_batch_size': 8, 'do_train': True}
args = TrainingArguments(**args_dict)

In [5]:
model = AutoModelForSequenceClassification.from_pretrained('roberta-base', num_labels=19)

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.decoder.weight', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.weight', 'lm_head.layer_norm.weight', 'lm_head.bias', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifi

In [6]:
trainer = Trainer(
    model, 
    args,
    train_dataset=data_hf_tokenized["train"],
    eval_dataset=data_hf_tokenized["test"],
    data_collator=DataCollatorWithPadding(tokenizer),
)
trainer.train()

/usr/local/lib/python3.9/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 11883
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 4458


Saving model checkpoint to logs/checkpoint-500
Configuration saved in logs/checkpoint-500/config.json
Model weights saved in logs/checkpoint-500/pytorch_model.bin
Saving model checkpoint to logs/checkpoint-1000
Configuration saved in logs/checkpoint-1000/config.json
Model weights saved in logs/checkpoint-1000/pytorch_model.bin
Saving model checkpoint to logs/checkpoint-1500
Configuration saved in logs/checkpoint-1500/config.json
Model weights saved in logs/checkpoint-1500/pytorch_model.bin
Saving model checkpoint to logs/checkpoint-2000
Configuration saved in logs/checkpoint-2000/config.json
Model weights saved in logs/checkpoint-2000/pytorch_model.bin
Saving model checkpoint to logs/checkpoint-2500
Configuration saved in logs/checkpoint-2500/config.json
Model weights saved in logs/checkpoint-2500/pytorch_model.bin
Saving model checkpoint to logs/checkpoint-3000
Configuration saved in logs/checkpoint-3000/config.json
Model weights saved in logs/checkpoint-3000/pytorch_model.bin
Saving 

TrainOutput(global_step=4458, training_loss=0.8849190480509057, metrics={'train_runtime': 74409.2364, 'train_samples_per_second': 0.479, 'train_steps_per_second': 0.06, 'total_flos': 4731926386857384.0, 'train_loss': 0.8849190480509057, 'epoch': 3.0})

In [7]:
predictions = trainer.predict(data_hf_tokenized["test"])

***** Running Prediction *****
  Num examples = 2097
  Batch size = 8


In [9]:
trainer.save_model('model_roberta_trained')

Saving model checkpoint to model_roberta_trained
Configuration saved in model_roberta_trained/config.json
Model weights saved in model_roberta_trained/pytorch_model.bin


Обучила ещё distilbert в коллабе, но там результат немного хуже.
Пользовалась этим:
https://github.com/ThilinaRajapakse/pytorch-transformers-classification
https://github.com/huggingface/transformers/tree/main/src/transformers